# Preprocessing Translation Data

### Function for expanding english contractions

source: https://gist.github.com/nealrs/96342d8231b75cf4bb82

In [1]:
import numpy as np
from __future__ import division
import io
import unicodedata
import nltk
from nltk import word_tokenize
import string
import re
import random


#source: https://gist.github.com/nealrs/96342d8231b75cf4bb82
cList = {
  "ain't": "am not",
  "aren't": "are not",
  "can't": "cannot",
  "can't've": "cannot have",
  "'cause": "because",
  "could've": "could have",
  "couldn't": "could not",
  "couldn't've": "could not have",
  "didn't": "did not",
  "doesn't": "does not",
  "don't": "do not",
  "hadn't": "had not",
  "hadn't've": "had not have",
  "hasn't": "has not",
  "haven't": "have not",
  "he'd": "he would",
  "he'd've": "he would have",
  "he'll": "he will",
  "he'll've": "he will have",
  "he's": "he is",
  "how'd": "how did",
  "how'd'y": "how do you",
  "how'll": "how will",
  "how's": "how is",
  "I'd": "I would",
  "I'd've": "I would have",
  "I'll": "I will",
  "I'll've": "I will have",
  "I'm": "I am",
  "I've": "I have",
  "isn't": "is not",
  "it'd": "it had",
  "it'd've": "it would have",
  "it'll": "it will",
  "it'll've": "it will have",
  "it's": "it is",
  "let's": "let us",
  "ma'am": "madam",
  "mayn't": "may not",
  "might've": "might have",
  "mightn't": "might not",
  "mightn't've": "might not have",
  "must've": "must have",
  "mustn't": "must not",
  "mustn't've": "must not have",
  "needn't": "need not",
  "needn't've": "need not have",
  "o'clock": "of the clock",
  "oughtn't": "ought not",
  "oughtn't've": "ought not have",
  "shan't": "shall not",
  "sha'n't": "shall not",
  "shan't've": "shall not have",
  "she'd": "she would",
  "she'd've": "she would have",
  "she'll": "she will",
  "she'll've": "she will have",
  "she's": "she is",
  "should've": "should have",
  "shouldn't": "should not",
  "shouldn't've": "should not have",
  "so've": "so have",
  "so's": "so is",
  "that'd": "that would",
  "that'd've": "that would have",
  "that's": "that is",
  "there'd": "there had",
  "there'd've": "there would have",
  "there's": "there is",
  "they'd": "they would",
  "they'd've": "they would have",
  "they'll": "they will",
  "they'll've": "they will have",
  "they're": "they are",
  "they've": "they have",
  "to've": "to have",
  "wasn't": "was not",
  "we'd": "we had",
  "we'd've": "we would have",
  "we'll": "we will",
  "we'll've": "we will have",
  "we're": "we are",
  "we've": "we have",
  "weren't": "were not",
  "what'll": "what will",
  "what'll've": "what will have",
  "what're": "what are",
  "what's": "what is",
  "what've": "what have",
  "when's": "when is",
  "when've": "when have",
  "where'd": "where did",
  "where's": "where is",
  "where've": "where have",
  "who'll": "who will",
  "who'll've": "who will have",
  "who's": "who is",
  "who've": "who have",
  "why's": "why is",
  "why've": "why have",
  "will've": "will have",
  "won't": "will not",
  "won't've": "will not have",
  "would've": "would have",
  "wouldn't": "would not",
  "wouldn't've": "would not have",
  "y'all": "you all",
  "y'alls": "you alls",
  "y'all'd": "you all would",
  "y'all'd've": "you all would have",
  "y'all're": "you all are",
  "y'all've": "you all have",
  "you'd": "you had",
  "you'd've": "you would have",
  "you'll": "you you will",
  "you'll've": "you you will have",
  "you're": "you are",
  "you've": "you have"
}

c_re = re.compile('(%s)' % '|'.join(cList.keys()))

def expandContractions(text, c_re=c_re):
    def replace(match):
        return cList[match.group(0)]
    return c_re.sub(replace, text)

### Loading Translation Data

Splitting the data into eng and beng.
eng will contain the list of English lines, and beng will contain the corresponding list of Bengali lines.


Source of data: http://www.manythings.org/anki/ (downloaded ben-eng)

In [2]:
filename = 'ben.txt'
#Datasource: http://www.manythings.org/anki/
    
# http://stackoverflow.com/a/518232/2809427
def unicodeToAscii(s):
    return ''.join(
        c for c in unicodedata.normalize('NFD', s)
        if unicodedata.category(c) != 'Mn'
    )
    
def normalizeString(s):
    s = unicodeToAscii(expandContractions(s.lower().strip()))
    s = re.sub(r"([.!?,\"])", r" ", s)
    return s
    
def loaddata(filename):
    file = io.open(filename,'r')
    eng=[]
    beng = []
    for line in file.readlines():
        lang_pair = line.split('\t')
        lang_pair[0] = normalizeString(lang_pair[0])
        lang_pair[1] = normalizeString(lang_pair[1])
        eng.append(word_tokenize(lang_pair[0]))
        beng.append(word_tokenize(lang_pair[1]))
    file.close()
    return eng,beng

eng,beng = loaddata(filename)

#Example:
sample = random.randint(0,len(eng))
print "Example Sample #"+str(sample)+":\n"
string = "ENGLISH:"
for i in xrange(0,len(eng[sample])):
    string+=" "+eng[sample][i]
print string
    
string = "\nBENGALI:"
for i in xrange(0,len(beng[sample])):
    string+=" "+beng[sample][i]
print string


Example Sample #646:

ENGLISH: tom 's right

BENGALI: টমই ঠিক।


### Creating separate vocabulary lists for English words and Bengali words

The index of vocabulary will represent the numerical representation of the word which is the value of vocabulary at that index. 


In [3]:
import numpy as np

vocab_eng=[]
vocab_eng.append('<PAD>')
vocab_eng.append('<EOS>')

vocab_beng=[]
vocab_beng.append('<PAD>')
vocab_beng.append('<EOS>')

#The index of vocab will serve as an integer representation of the word

vectorized_eng = []
vectorized_beng = []

for i in xrange(len(eng)):
    
    vectorized_eng_line = []
    for word in eng[i]:
        if word not in vocab_eng:
            vocab_eng.append(word)
            vectorized_eng_line.append(vocab_eng.index(word))
        else:
            vectorized_eng_line.append(vocab_eng.index(word))
    vectorized_eng.append(vectorized_eng_line)
    
    vectorized_beng_line = []
    for word in beng[i]:
        if word not in vocab_beng:
            vocab_beng.append(word)
            vectorized_beng_line.append(vocab_beng.index(word))
        else:
            vectorized_beng_line.append(vocab_beng.index(word))
    vectorized_beng.append(vectorized_beng_line)
    
    

### Creating training dataset for word2vec embedding

if the sentence is "I am alright"

then for the word 'am', the context words with window size 1 will be "I" and "alright"
i.e ["I","alright"]

For 'I' the context words will be "PAD" and "am"

For 'alright' the context words will be "am" and "PAD"

PAD represents empty and EOS represents end of sentence.

Later lots of pads may be applied after the end of sentence to fit sequence length.

So I also added the word PAD with context words being PADs, and PAD and EOS for embedding.

In this way, first, from each sentence, I am creating a list of words, and corresponding list of context words.
Doing the same thing for

In [4]:
words_eng = []
contexts_eng = []

words_beng = []
contexts_beng = []

words_eng.append(vocab_eng.index('<PAD>'))
contexts_eng.append([vocab_eng.index('<EOS>'),vocab_eng.index('<PAD>')])
words_eng.append(vocab_eng.index('<PAD>'))
contexts_eng.append([vocab_eng.index('<PAD>'),vocab_eng.index('<PAD>')])

words_beng.append(vocab_beng.index('<PAD>'))
contexts_beng.append([vocab_beng.index('<EOS>'),vocab_beng.index('<PAD>')])
words_beng.append(vocab_beng.index('<PAD>'))
contexts_beng.append([vocab_beng.index('<PAD>'),vocab_beng.index('<PAD>')])


for i in xrange(len(vectorized_eng)):
    
    for j in xrange(0,len(vectorized_eng[i])):
        
        context1=0
        context2=0
        
        if j==0:
            context1 = vocab_eng.index('<PAD>')
            if j!=len(vectorized_eng[i])-1:
                context2 = vectorized_eng[i][j+1]
        if j==len(vectorized_eng[i])-1:
            context2=vocab_eng.index('<EOS>')
            if j!=0:
                context1 = vectorized_eng[i][j-1]
        if j>0 and j<len(vectorized_eng[i])-1:
            context1 = vectorized_eng[i][j-1]
            context2 = vectorized_eng[i][j+1]
        
        words_eng.append(vectorized_eng[i][j])
        contexts_eng.append([context1,context2])
    
    rand = random.randint(0,3)
    if rand == 1: #reduce the freuency of <EOS> for training data
        words_eng.append(vocab_eng.index('<EOS>'))
        context1 = vectorized_eng[i][len(vectorized_eng[i])-1]
        context2 = vocab_eng.index('<PAD>')
        contexts_eng.append([context1,context2])
    
    for j in xrange(0,len(vectorized_beng[i])):
        
        context1=0
        context2=0
        
        if j==0:
            context1 = vocab_beng.index('<PAD>')
            if j!=len(vectorized_beng[i])-1:
                context2 = vectorized_beng[i][j+1]
        if j==len(vectorized_beng[i])-1:
            context2=vocab_beng.index('<EOS>')
            if j!=0:
                context1 = vectorized_beng[i][j-1]
        if j>0 and j<len(vectorized_beng[i])-1:
            context1 = vectorized_beng[i][j-1]
            context2 = vectorized_beng[i][j+1]
        
        words_beng.append(vectorized_beng[i][j])
        contexts_beng.append([context1,context2])
    
    rand = random.randint(0,3)
    if rand == 1: #reduce the freuency of <EOS> for training data
        words_beng.append(vocab_beng.index('<EOS>'))
        context1 = vectorized_beng[i][len(vectorized_beng[i])-1]
        context2 = vocab_beng.index('<PAD>')
        contexts_beng.append([context1,context2])
    
    
            

If word = "am" and context = ["I","alright"],
then, here I will reconstrcut the data as:

input = "am"
output = "I"
and 
input = "am"
label = "alright"

Like this I will construct a list of all training inputs (words) and training outputs\labels (context words)

embd_inputs_eng will contain all the English training inputs.
embd_labels_eng will contain all the English training labels.

embd_inputs_beng will contain all the Bengali training inputs.
embd_labels_beng will contain all the Bengali training labels.

In [5]:
embd_inputs_eng = []
embd_labels_eng = []
for i in xrange(len(contexts_eng)):
    for context in contexts_eng[i]:
        embd_inputs_eng.append(words_eng[i])
        embd_labels_eng.append(context)
embd_inputs_eng = np.asarray(embd_inputs_eng,np.int32)
embd_labels_eng = np.asarray(embd_labels_eng,np.int32)

embd_inputs_beng = []
embd_labels_beng = []
for i in xrange(len(contexts_beng)):
    for context in contexts_beng[i]:
        embd_inputs_beng.append(words_beng[i])
        embd_labels_beng.append(context)
embd_inputs_beng = np.asarray(embd_inputs_beng,np.int32)
embd_labels_beng = np.asarray(embd_labels_beng,np.int32)
    

### Function for generating mini-batches from the total training set

In [6]:
batch_size = 128

def generate_batch(inputs,labels,batch_size):
    rand = random.sample((np.arange(len(inputs))),batch_size)
    batch_inputs=[]
    batch_labels=[]
    for i in xrange(batch_size):
        batch_inputs.append(inputs[int(rand[i])])
        batch_labels.append(labels[int(rand[i])])
    batch_inputs = np.asarray(batch_inputs,np.int32)
    batch_labels = np.asarray(batch_labels,np.int32)
    return batch_inputs,batch_labels
    

### Preparing for word2vec embedding

In [7]:
import tensorflow as tf
import math

#https://www.tensorflow.org/tutorials/word2vec
embedding_size = 256
vocabulary_size_eng = len(vocab_eng)
vocabulary_size_beng = len(vocab_beng)

# Placeholders for inputs
train_inputs = tf.placeholder(tf.int32, shape=[batch_size])
train_labels = tf.placeholder(tf.int32, shape=[batch_size,1])


### Training for word2vec embedding (For English words)

See: https://www.tensorflow.org/tutorials/word2vec

for details of word2vec and code description

In [8]:
embeddings_eng = tf.Variable(
    tf.random_uniform([vocabulary_size_eng, embedding_size], -1.0, 1.0))

nce_weights_eng = tf.Variable(
  tf.truncated_normal([vocabulary_size_eng, embedding_size],
                      stddev=1.0 / math.sqrt(embedding_size)))
nce_biases_eng = tf.Variable(tf.zeros([vocabulary_size_eng]))

# Initializing the variables
init = tf.global_variables_initializer()

In [9]:
embed_eng = tf.nn.embedding_lookup(embeddings_eng, train_inputs)

# Compute the NCE loss, using a sample of the negative labels each time.
loss = tf.reduce_mean(
  tf.nn.nce_loss(weights=nce_weights_eng,
                 biases=nce_biases_eng,
                 labels=train_labels,
                 inputs=embed_eng,
                 num_sampled=10, 
                 num_classes=vocabulary_size_eng)) #num_sampled = no. of negative samples

# We use the SGD optimizer.
optimizer = tf.train.GradientDescentOptimizer(learning_rate=1.0).minimize(loss)

            


In [10]:

with tf.Session() as sess:
    sess.run(init)
    convergence_threshold = 0.5
    training_iters = 500*(int((len(embd_inputs_eng))/batch_size))
    step=0
    n=5
    last_n_losses = np.zeros((n),np.float32)
    
    while step<training_iters:
        
        batch_inputs,batch_labels = generate_batch(embd_inputs_eng,embd_labels_eng,batch_size)
        
        feed_dict = {train_inputs: batch_inputs, train_labels: batch_labels.reshape((-1,1))}
        
        _, np_embedding_eng, cur_loss = sess.run([optimizer, embeddings_eng, loss], feed_dict=feed_dict)
        
        print "Iter "+str(step)+", loss = "+str(cur_loss)
        
        last_n_losses[step%n]=cur_loss
        
        if step>=n:
            if np.mean(last_n_losses)<=convergence_threshold:
                break
        step+=1
                
print "\nOptimization Finished\n"

Iter 0, loss = 39.3585
Iter 1, loss = 31.6442
Iter 2, loss = 40.2299
Iter 3, loss = 26.6633
Iter 4, loss = 30.0873
Iter 5, loss = 35.8647
Iter 6, loss = 32.8691
Iter 7, loss = 21.8486
Iter 8, loss = 32.4225
Iter 9, loss = 28.3651
Iter 10, loss = 48.7023
Iter 11, loss = 46.4276
Iter 12, loss = 37.27
Iter 13, loss = 26.59
Iter 14, loss = 33.1536
Iter 15, loss = 32.5372
Iter 16, loss = 31.064
Iter 17, loss = 34.2121
Iter 18, loss = 22.984
Iter 19, loss = 24.2449
Iter 20, loss = 19.9898
Iter 21, loss = 35.1426
Iter 22, loss = 27.0518
Iter 23, loss = 29.7837
Iter 24, loss = 32.0492
Iter 25, loss = 33.0099
Iter 26, loss = 32.5165
Iter 27, loss = 27.6404
Iter 28, loss = 28.6027
Iter 29, loss = 32.3248
Iter 30, loss = 32.476
Iter 31, loss = 44.3097
Iter 32, loss = 20.6836
Iter 33, loss = 20.0285
Iter 34, loss = 36.7078
Iter 35, loss = 13.2457
Iter 36, loss = 27.3928
Iter 37, loss = 27.1477
Iter 38, loss = 33.4294
Iter 39, loss = 36.0049
Iter 40, loss = 19.6766
Iter 41, loss = 35.3159
Iter 42, 

Iter 440, loss = 3.02764
Iter 441, loss = 5.65793
Iter 442, loss = 9.77245
Iter 443, loss = 16.0593
Iter 444, loss = 7.14461
Iter 445, loss = 4.70673
Iter 446, loss = 12.1097
Iter 447, loss = 12.0163
Iter 448, loss = 5.43926
Iter 449, loss = 4.99015
Iter 450, loss = 11.4669
Iter 451, loss = 5.30793
Iter 452, loss = 9.00635
Iter 453, loss = 11.8426
Iter 454, loss = 16.638
Iter 455, loss = 3.96731
Iter 456, loss = 27.186
Iter 457, loss = 22.846
Iter 458, loss = 2.82856
Iter 459, loss = 4.38539
Iter 460, loss = 21.2008
Iter 461, loss = 20.0327
Iter 462, loss = 5.45902
Iter 463, loss = 5.80435
Iter 464, loss = 13.9595
Iter 465, loss = 9.95827
Iter 466, loss = 17.3901
Iter 467, loss = 9.68397
Iter 468, loss = 8.19197
Iter 469, loss = 4.87782
Iter 470, loss = 2.92772
Iter 471, loss = 19.424
Iter 472, loss = 5.56829
Iter 473, loss = 14.7704
Iter 474, loss = 6.41557
Iter 475, loss = 5.42984
Iter 476, loss = 21.3761
Iter 477, loss = 8.62017
Iter 478, loss = 13.2457
Iter 479, loss = 9.96034
Iter

Iter 882, loss = 10.1034
Iter 883, loss = 17.5145
Iter 884, loss = 2.24344
Iter 885, loss = 15.8996
Iter 886, loss = 2.58958
Iter 887, loss = 5.93839
Iter 888, loss = 3.97147
Iter 889, loss = 9.8921
Iter 890, loss = 3.01798
Iter 891, loss = 16.3029
Iter 892, loss = 8.44746
Iter 893, loss = 16.0074
Iter 894, loss = 27.3631
Iter 895, loss = 3.75425
Iter 896, loss = 3.76579
Iter 897, loss = 16.0968
Iter 898, loss = 4.68273
Iter 899, loss = 2.85567
Iter 900, loss = 2.69618
Iter 901, loss = 9.38997
Iter 902, loss = 10.9681
Iter 903, loss = 8.77945
Iter 904, loss = 2.14716
Iter 905, loss = 2.77858
Iter 906, loss = 10.4172
Iter 907, loss = 9.92313
Iter 908, loss = 2.47969
Iter 909, loss = 3.03085
Iter 910, loss = 2.29978
Iter 911, loss = 8.87677
Iter 912, loss = 4.39449
Iter 913, loss = 3.16196
Iter 914, loss = 3.79102
Iter 915, loss = 10.304
Iter 916, loss = 4.10586
Iter 917, loss = 2.61353
Iter 918, loss = 2.16375
Iter 919, loss = 12.1607
Iter 920, loss = 9.1369
Iter 921, loss = 4.16425
Ite

Iter 1330, loss = 2.65706
Iter 1331, loss = 16.0479
Iter 1332, loss = 2.54318
Iter 1333, loss = 2.59765
Iter 1334, loss = 9.72163
Iter 1335, loss = 15.303
Iter 1336, loss = 14.7342
Iter 1337, loss = 8.9456
Iter 1338, loss = 9.71972
Iter 1339, loss = 2.48976
Iter 1340, loss = 1.86516
Iter 1341, loss = 17.1419
Iter 1342, loss = 9.02595
Iter 1343, loss = 2.63455
Iter 1344, loss = 2.22273
Iter 1345, loss = 9.21117
Iter 1346, loss = 1.83928
Iter 1347, loss = 3.30402
Iter 1348, loss = 2.94847
Iter 1349, loss = 2.62864
Iter 1350, loss = 9.16959
Iter 1351, loss = 9.2196
Iter 1352, loss = 2.33924
Iter 1353, loss = 10.1451
Iter 1354, loss = 2.31045
Iter 1355, loss = 8.92487
Iter 1356, loss = 3.1674
Iter 1357, loss = 3.13575
Iter 1358, loss = 10.0058
Iter 1359, loss = 2.06871
Iter 1360, loss = 2.69889
Iter 1361, loss = 2.30926
Iter 1362, loss = 3.10073
Iter 1363, loss = 3.39472
Iter 1364, loss = 2.31996
Iter 1365, loss = 2.03189
Iter 1366, loss = 8.46118
Iter 1367, loss = 2.46612
Iter 1368, loss 

Iter 1777, loss = 2.2713
Iter 1778, loss = 2.91576
Iter 1779, loss = 2.59735
Iter 1780, loss = 1.87072
Iter 1781, loss = 2.02187
Iter 1782, loss = 3.6032
Iter 1783, loss = 1.94452
Iter 1784, loss = 10.321
Iter 1785, loss = 2.93151
Iter 1786, loss = 1.6605
Iter 1787, loss = 17.1207
Iter 1788, loss = 2.75735
Iter 1789, loss = 1.9485
Iter 1790, loss = 2.21107
Iter 1791, loss = 3.62216
Iter 1792, loss = 2.20268
Iter 1793, loss = 9.38811
Iter 1794, loss = 5.19402
Iter 1795, loss = 2.20749
Iter 1796, loss = 2.24071
Iter 1797, loss = 1.78018
Iter 1798, loss = 2.09934
Iter 1799, loss = 3.23016
Iter 1800, loss = 2.45474
Iter 1801, loss = 2.40669
Iter 1802, loss = 2.37982
Iter 1803, loss = 9.84266
Iter 1804, loss = 3.03805
Iter 1805, loss = 2.00995
Iter 1806, loss = 1.82413
Iter 1807, loss = 9.27502
Iter 1808, loss = 2.4858
Iter 1809, loss = 4.85014
Iter 1810, loss = 3.87799
Iter 1811, loss = 2.14676
Iter 1812, loss = 1.73053
Iter 1813, loss = 1.46479
Iter 1814, loss = 2.46903
Iter 1815, loss = 

...

Iter 170946, loss = 0.799521
Iter 170947, loss = 1.02243
Iter 170948, loss = 1.26825
Iter 170949, loss = 1.30285
Iter 170950, loss = 1.00194
Iter 170951, loss = 1.86681
Iter 170952, loss = 1.07103
Iter 170953, loss = 1.40094
Iter 170954, loss = 1.15412
Iter 170955, loss = 1.26498
Iter 170956, loss = 1.36447
Iter 170957, loss = 1.02414
Iter 170958, loss = 0.882158
Iter 170959, loss = 1.21303
Iter 170960, loss = 1.17389
Iter 170961, loss = 1.49453
Iter 170962, loss = 1.07761
Iter 170963, loss = 1.04947
Iter 170964, loss = 1.43912
Iter 170965, loss = 0.963702
Iter 170966, loss = 1.51023
Iter 170967, loss = 1.45623
Iter 170968, loss = 0.85643
Iter 170969, loss = 1.22259
Iter 170970, loss = 1.01381
Iter 170971, loss = 0.831367
Iter 170972, loss = 1.17752
Iter 170973, loss = 1.11409
Iter 170974, loss = 1.26615
Iter 170975, loss = 1.00004
Iter 170976, loss = 0.891308
Iter 170977, loss = 0.996527
Iter 170978, loss = 1.35332
Iter 170979, loss = 1.46342
Iter 170980, loss = 1.15603
Iter 170981, l

Iter 171305, loss = 1.0259
Iter 171306, loss = 1.41727
Iter 171307, loss = 1.43029
Iter 171308, loss = 1.55575
Iter 171309, loss = 0.994437
Iter 171310, loss = 1.77185
Iter 171311, loss = 0.789416
Iter 171312, loss = 1.49473
Iter 171313, loss = 1.35032
Iter 171314, loss = 1.13674
Iter 171315, loss = 1.80783
Iter 171316, loss = 1.03968
Iter 171317, loss = 1.13084
Iter 171318, loss = 1.23442
Iter 171319, loss = 1.18026
Iter 171320, loss = 0.695423
Iter 171321, loss = 1.54329
Iter 171322, loss = 2.19676
Iter 171323, loss = 1.0705
Iter 171324, loss = 0.979199
Iter 171325, loss = 1.48543
Iter 171326, loss = 1.08386
Iter 171327, loss = 1.1079
Iter 171328, loss = 1.28688
Iter 171329, loss = 1.03353
Iter 171330, loss = 1.17676
Iter 171331, loss = 1.85389
Iter 171332, loss = 1.79541
Iter 171333, loss = 1.00958
Iter 171334, loss = 1.07959
Iter 171335, loss = 1.06682
Iter 171336, loss = 1.14181
Iter 171337, loss = 0.799016
Iter 171338, loss = 2.2653
Iter 171339, loss = 1.28003
Iter 171340, loss =

Iter 171662, loss = 0.998512
Iter 171663, loss = 1.11672
Iter 171664, loss = 2.19279
Iter 171665, loss = 1.4904
Iter 171666, loss = 1.50818
Iter 171667, loss = 1.14014
Iter 171668, loss = 1.01534
Iter 171669, loss = 1.08304
Iter 171670, loss = 1.10262
Iter 171671, loss = 0.823339
Iter 171672, loss = 0.78855
Iter 171673, loss = 1.37882
Iter 171674, loss = 0.875373
Iter 171675, loss = 1.27588
Iter 171676, loss = 1.13636
Iter 171677, loss = 1.03754
Iter 171678, loss = 1.42901
Iter 171679, loss = 1.40032
Iter 171680, loss = 1.91009
Iter 171681, loss = 1.01396
Iter 171682, loss = 1.05739
Iter 171683, loss = 1.73936
Iter 171684, loss = 1.63934
Iter 171685, loss = 1.84585
Iter 171686, loss = 1.87294
Iter 171687, loss = 0.977619
Iter 171688, loss = 1.26987
Iter 171689, loss = 1.43066
Iter 171690, loss = 1.05894
Iter 171691, loss = 1.02332
Iter 171692, loss = 0.965838
Iter 171693, loss = 1.25639
Iter 171694, loss = 1.38873
Iter 171695, loss = 1.42514
Iter 171696, loss = 1.02254
Iter 171697, los

Iter 172036, loss = 1.14521
Iter 172037, loss = 1.42533
Iter 172038, loss = 0.832677
Iter 172039, loss = 1.05454
Iter 172040, loss = 1.11405
Iter 172041, loss = 1.32026
Iter 172042, loss = 0.960039
Iter 172043, loss = 2.45559
Iter 172044, loss = 0.989823
Iter 172045, loss = 1.69766
Iter 172046, loss = 1.06686
Iter 172047, loss = 0.969731
Iter 172048, loss = 0.758366
Iter 172049, loss = 1.54384
Iter 172050, loss = 1.66931
Iter 172051, loss = 1.33676
Iter 172052, loss = 1.02676
Iter 172053, loss = 1.55507
Iter 172054, loss = 1.22623
Iter 172055, loss = 1.43108
Iter 172056, loss = 1.10982
Iter 172057, loss = 1.12923
Iter 172058, loss = 1.14582
Iter 172059, loss = 1.31269
Iter 172060, loss = 0.898955
Iter 172061, loss = 1.32248
Iter 172062, loss = 1.1216
Iter 172063, loss = 0.925425
Iter 172064, loss = 1.44772
Iter 172065, loss = 0.832175
Iter 172066, loss = 1.03451
Iter 172067, loss = 1.34497
Iter 172068, loss = 1.37157
Iter 172069, loss = 1.65456
Iter 172070, loss = 1.18798
Iter 172071, 

Iter 172430, loss = 1.30145
Iter 172431, loss = 1.4618
Iter 172432, loss = 1.26438
Iter 172433, loss = 1.14211
Iter 172434, loss = 1.64245
Iter 172435, loss = 1.19363
Iter 172436, loss = 0.939318
Iter 172437, loss = 1.48732
Iter 172438, loss = 1.51522
Iter 172439, loss = 1.5289
Iter 172440, loss = 0.735392
Iter 172441, loss = 1.13756
Iter 172442, loss = 1.22212
Iter 172443, loss = 1.85378
Iter 172444, loss = 1.10971
Iter 172445, loss = 1.24304
Iter 172446, loss = 1.20319
Iter 172447, loss = 0.970834
Iter 172448, loss = 1.04503
Iter 172449, loss = 0.966331
Iter 172450, loss = 0.943213
Iter 172451, loss = 1.71692
Iter 172452, loss = 1.19416
Iter 172453, loss = 1.18727
Iter 172454, loss = 1.77249
Iter 172455, loss = 1.25295
Iter 172456, loss = 1.06173
Iter 172457, loss = 1.31235
Iter 172458, loss = 1.54665
Iter 172459, loss = 2.0763
Iter 172460, loss = 1.01453
Iter 172461, loss = 1.34968
Iter 172462, loss = 1.36245
Iter 172463, loss = 1.07693
Iter 172464, loss = 1.23457
Iter 172465, loss 

### Training for word2vec embedding (For Bengali words)

See: https://www.tensorflow.org/tutorials/word2vec

for details of word2vec and code description

In [11]:
embeddings_beng = tf.Variable(
    tf.random_uniform([vocabulary_size_beng, embedding_size], -1.0, 1.0))

nce_weights_beng = tf.Variable(
  tf.truncated_normal([vocabulary_size_beng, embedding_size],
                      stddev=1.0 / math.sqrt(embedding_size)))
nce_biases_beng = tf.Variable(tf.zeros([vocabulary_size_beng]))

# Initializing the variables
init = tf.global_variables_initializer()

In [12]:
embed_beng = tf.nn.embedding_lookup(embeddings_beng, train_inputs)

# Compute the NCE loss, using a sample of the negative labels each time.
loss = tf.reduce_mean(
  tf.nn.nce_loss(weights=nce_weights_beng,
                 biases=nce_biases_beng,
                 labels=train_labels,
                 inputs=embed_beng,
                 num_sampled=10, 
                 num_classes=vocabulary_size_beng)) #num_sampled = no. of negative samples

# We use the SGD optimizer.
optimizer = tf.train.GradientDescentOptimizer(learning_rate=1.0).minimize(loss)

            


In [13]:

with tf.Session() as sess:
    sess.run(init)
    convergence_threshold = 0.5
    training_iters = 500*(int((len(embd_inputs_beng))/batch_size))
    step=0
    n=5
    last_n_losses = np.zeros((n),np.float32)
    while step<training_iters:
        
        batch_inputs,batch_labels = generate_batch(embd_inputs_beng,embd_labels_beng,batch_size)
        
        feed_dict = {train_inputs: batch_inputs, train_labels: batch_labels.reshape((-1,1))}
        _, np_embedding_beng, cur_loss = sess.run([optimizer, embeddings_beng, loss], feed_dict=feed_dict)
        
        print "Iter "+str(step)+", loss = "+str(cur_loss)
        last_n_losses[step%n]=cur_loss
        if step>=n:
            if np.mean(last_n_losses)<=convergence_threshold:
                break
        step+=1
                
print "\nOptimization Finished\n"

Iter 0, loss = 35.9691
Iter 1, loss = 49.5002
Iter 2, loss = 50.4004
Iter 3, loss = 47.2024
Iter 4, loss = 44.8602
Iter 5, loss = 33.4372
Iter 6, loss = 45.144
Iter 7, loss = 42.9548
Iter 8, loss = 34.0341
Iter 9, loss = 47.3467
Iter 10, loss = 40.0691
Iter 11, loss = 28.1972
Iter 12, loss = 33.3716
Iter 13, loss = 40.1549
Iter 14, loss = 36.2827
Iter 15, loss = 29.2871
Iter 16, loss = 39.3284
Iter 17, loss = 46.7744
Iter 18, loss = 32.4007
Iter 19, loss = 35.5793
Iter 20, loss = 25.8909
Iter 21, loss = 19.593
Iter 22, loss = 50.6388
Iter 23, loss = 35.1734
Iter 24, loss = 36.5541
Iter 25, loss = 39.3813
Iter 26, loss = 35.6049
Iter 27, loss = 37.1966
Iter 28, loss = 36.6852
Iter 29, loss = 25.8813
Iter 30, loss = 31.9816
Iter 31, loss = 43.3429
Iter 32, loss = 34.9434
Iter 33, loss = 32.664
Iter 34, loss = 43.5259
Iter 35, loss = 24.7643
Iter 36, loss = 32.2928
Iter 37, loss = 41.8095
Iter 38, loss = 33.5225
Iter 39, loss = 27.3225
Iter 40, loss = 30.0497
Iter 41, loss = 33.8994
Iter 

Iter 412, loss = 14.5534
Iter 413, loss = 11.7323
Iter 414, loss = 30.9501
Iter 415, loss = 9.72766
Iter 416, loss = 19.0803
Iter 417, loss = 19.3172
Iter 418, loss = 20.7205
Iter 419, loss = 15.7191
Iter 420, loss = 26.8758
Iter 421, loss = 21.816
Iter 422, loss = 12.6522
Iter 423, loss = 9.62298
Iter 424, loss = 20.7112
Iter 425, loss = 13.9425
Iter 426, loss = 21.5653
Iter 427, loss = 28.4696
Iter 428, loss = 29.5778
Iter 429, loss = 14.909
Iter 430, loss = 23.2868
Iter 431, loss = 15.961
Iter 432, loss = 9.64631
Iter 433, loss = 18.7788
Iter 434, loss = 10.6526
Iter 435, loss = 33.269
Iter 436, loss = 13.9376
Iter 437, loss = 9.87778
Iter 438, loss = 21.6048
Iter 439, loss = 25.9955
Iter 440, loss = 31.0425
Iter 441, loss = 3.57249
Iter 442, loss = 8.16925
Iter 443, loss = 6.29447
Iter 444, loss = 25.3494
Iter 445, loss = 12.0253
Iter 446, loss = 14.2541
Iter 447, loss = 30.1637
Iter 448, loss = 21.8399
Iter 449, loss = 33.6122
Iter 450, loss = 13.1496
Iter 451, loss = 18.5658
Iter

Iter 836, loss = 8.2638
Iter 837, loss = 20.812
Iter 838, loss = 26.3357
Iter 839, loss = 17.193
Iter 840, loss = 18.8465
Iter 841, loss = 4.31056
Iter 842, loss = 14.4022
Iter 843, loss = 12.3138
Iter 844, loss = 18.1489
Iter 845, loss = 9.566
Iter 846, loss = 11.1751
Iter 847, loss = 14.9445
Iter 848, loss = 12.4523
Iter 849, loss = 12.175
Iter 850, loss = 4.86253
Iter 851, loss = 11.6972
Iter 852, loss = 5.18986
Iter 853, loss = 5.62587
Iter 854, loss = 11.2047
Iter 855, loss = 12.0177
Iter 856, loss = 15.3489
Iter 857, loss = 8.7623
Iter 858, loss = 20.8863
Iter 859, loss = 12.4941
Iter 860, loss = 22.3918
Iter 861, loss = 16.8836
Iter 862, loss = 6.55592
Iter 863, loss = 18.6285
Iter 864, loss = 24.4247
Iter 865, loss = 24.7784
Iter 866, loss = 13.3267
Iter 867, loss = 13.4592
Iter 868, loss = 17.1584
Iter 869, loss = 18.1031
Iter 870, loss = 9.73823
Iter 871, loss = 19.4825
Iter 872, loss = 18.4906
Iter 873, loss = 19.3341
Iter 874, loss = 27.89
Iter 875, loss = 6.72272
Iter 876,

Iter 1265, loss = 4.31599
Iter 1266, loss = 4.56503
Iter 1267, loss = 18.0176
Iter 1268, loss = 2.5235
Iter 1269, loss = 18.1742
Iter 1270, loss = 11.934
Iter 1271, loss = 11.5666
Iter 1272, loss = 12.6385
Iter 1273, loss = 19.6315
Iter 1274, loss = 6.30733
Iter 1275, loss = 10.955
Iter 1276, loss = 17.5808
Iter 1277, loss = 3.63565
Iter 1278, loss = 3.57711
Iter 1279, loss = 1.42798
Iter 1280, loss = 9.67196
Iter 1281, loss = 19.6089
Iter 1282, loss = 5.95091
Iter 1283, loss = 17.1287
Iter 1284, loss = 4.68638
Iter 1285, loss = 4.16125
Iter 1286, loss = 2.83794
Iter 1287, loss = 9.96476
Iter 1288, loss = 2.50197
Iter 1289, loss = 8.32465
Iter 1290, loss = 10.435
Iter 1291, loss = 9.85358
Iter 1292, loss = 4.79633
Iter 1293, loss = 5.05374
Iter 1294, loss = 17.631
Iter 1295, loss = 21.3073
Iter 1296, loss = 11.0553
Iter 1297, loss = 9.86196
Iter 1298, loss = 12.6353
Iter 1299, loss = 3.63255
Iter 1300, loss = 9.0986
Iter 1301, loss = 3.27005
Iter 1302, loss = 10.6727
Iter 1303, loss = 

Iter 1672, loss = 5.95951
Iter 1673, loss = 4.25911
Iter 1674, loss = 12.1098
Iter 1675, loss = 2.78818
Iter 1676, loss = 4.62721
Iter 1677, loss = 2.66869
Iter 1678, loss = 17.9945
Iter 1679, loss = 3.47244
Iter 1680, loss = 18.9549
Iter 1681, loss = 2.32943
Iter 1682, loss = 3.05169
Iter 1683, loss = 3.03383
Iter 1684, loss = 4.51894
Iter 1685, loss = 10.3756
Iter 1686, loss = 16.5123
Iter 1687, loss = 9.85403
Iter 1688, loss = 2.51703
Iter 1689, loss = 13.013
Iter 1690, loss = 10.99
Iter 1691, loss = 12.033
Iter 1692, loss = 3.20075
Iter 1693, loss = 10.0286
Iter 1694, loss = 6.14657
Iter 1695, loss = 1.878
Iter 1696, loss = 12.2526
Iter 1697, loss = 3.81932
Iter 1698, loss = 17.2691
Iter 1699, loss = 10.9028
Iter 1700, loss = 9.63173
Iter 1701, loss = 6.8766
Iter 1702, loss = 2.24403
Iter 1703, loss = 20.0387
Iter 1704, loss = 4.15903
Iter 1705, loss = 7.48962
Iter 1706, loss = 2.36937
Iter 1707, loss = 10.4635
Iter 1708, loss = 9.36295
Iter 1709, loss = 2.87382
Iter 1710, loss = 3

...

Iter 33857, loss = 0.767404
Iter 33858, loss = 1.29352
Iter 33859, loss = 0.965266
Iter 33860, loss = 0.81784
Iter 33861, loss = 0.777534
Iter 33862, loss = 1.04524
Iter 33863, loss = 0.652808
Iter 33864, loss = 0.822072
Iter 33865, loss = 1.03018
Iter 33866, loss = 0.750131
Iter 33867, loss = 0.634372
Iter 33868, loss = 0.768089
Iter 33869, loss = 1.2835
Iter 33870, loss = 0.588443
Iter 33871, loss = 0.613628
Iter 33872, loss = 0.581921
Iter 33873, loss = 0.756096
Iter 33874, loss = 0.888368
Iter 33875, loss = 1.17247
Iter 33876, loss = 0.722904
Iter 33877, loss = 1.56647
Iter 33878, loss = 0.727185
Iter 33879, loss = 0.664876
Iter 33880, loss = 0.657622
Iter 33881, loss = 1.36437
Iter 33882, loss = 0.957432
Iter 33883, loss = 1.00067
Iter 33884, loss = 0.663841
Iter 33885, loss = 1.20852
Iter 33886, loss = 1.18224
Iter 33887, loss = 0.86871
Iter 33888, loss = 0.678681
Iter 33889, loss = 1.62837
Iter 33890, loss = 1.18559
Iter 33891, loss = 0.931986
Iter 33892, loss = 0.880308
Iter 33

Iter 34258, loss = 0.892045
Iter 34259, loss = 0.695376
Iter 34260, loss = 0.63412
Iter 34261, loss = 1.80522
Iter 34262, loss = 1.04604
Iter 34263, loss = 0.978374
Iter 34264, loss = 1.28954
Iter 34265, loss = 0.911342
Iter 34266, loss = 0.832262
Iter 34267, loss = 0.480111
Iter 34268, loss = 1.31385
Iter 34269, loss = 1.02183
Iter 34270, loss = 1.12605
Iter 34271, loss = 1.01073
Iter 34272, loss = 0.689139
Iter 34273, loss = 0.768548
Iter 34274, loss = 1.05604
Iter 34275, loss = 0.937805
Iter 34276, loss = 1.40623
Iter 34277, loss = 1.17657
Iter 34278, loss = 0.843548
Iter 34279, loss = 0.865215
Iter 34280, loss = 0.805453
Iter 34281, loss = 0.960863
Iter 34282, loss = 1.19074
Iter 34283, loss = 0.871571
Iter 34284, loss = 0.690059
Iter 34285, loss = 1.09177
Iter 34286, loss = 0.809567
Iter 34287, loss = 0.745023
Iter 34288, loss = 1.60844
Iter 34289, loss = 0.673474
Iter 34290, loss = 0.963269
Iter 34291, loss = 1.21272
Iter 34292, loss = 0.803594
Iter 34293, loss = 0.883599
Iter 34

Iter 34662, loss = 0.586972
Iter 34663, loss = 1.30298
Iter 34664, loss = 0.592607
Iter 34665, loss = 1.50152
Iter 34666, loss = 0.996319
Iter 34667, loss = 1.07488
Iter 34668, loss = 0.645107
Iter 34669, loss = 1.03959
Iter 34670, loss = 0.792899
Iter 34671, loss = 0.782969
Iter 34672, loss = 0.899925
Iter 34673, loss = 1.26846
Iter 34674, loss = 0.819843
Iter 34675, loss = 1.02921
Iter 34676, loss = 0.942559
Iter 34677, loss = 0.853189
Iter 34678, loss = 0.786955
Iter 34679, loss = 0.93065
Iter 34680, loss = 0.473196
Iter 34681, loss = 1.61387
Iter 34682, loss = 0.963419
Iter 34683, loss = 0.762249
Iter 34684, loss = 0.62706
Iter 34685, loss = 0.611625
Iter 34686, loss = 0.794268
Iter 34687, loss = 0.805901
Iter 34688, loss = 1.22401
Iter 34689, loss = 0.832062
Iter 34690, loss = 0.620209
Iter 34691, loss = 0.727239
Iter 34692, loss = 0.696388
Iter 34693, loss = 0.60471
Iter 34694, loss = 0.809606
Iter 34695, loss = 0.79807
Iter 34696, loss = 0.492993
Iter 34697, loss = 0.867605
Iter

Iter 35073, loss = 1.09718
Iter 35074, loss = 0.715647
Iter 35075, loss = 0.791224
Iter 35076, loss = 1.02466
Iter 35077, loss = 1.09057
Iter 35078, loss = 1.01265
Iter 35079, loss = 0.980408
Iter 35080, loss = 0.97393
Iter 35081, loss = 0.907492
Iter 35082, loss = 0.856533
Iter 35083, loss = 0.713586
Iter 35084, loss = 0.74088
Iter 35085, loss = 0.917934
Iter 35086, loss = 0.974782
Iter 35087, loss = 0.671778
Iter 35088, loss = 0.765314
Iter 35089, loss = 1.14891
Iter 35090, loss = 0.811357
Iter 35091, loss = 0.920538
Iter 35092, loss = 1.98197
Iter 35093, loss = 1.18512
Iter 35094, loss = 0.881265
Iter 35095, loss = 0.658746
Iter 35096, loss = 0.797721
Iter 35097, loss = 1.07956
Iter 35098, loss = 0.906721
Iter 35099, loss = 1.40458
Iter 35100, loss = 0.694804
Iter 35101, loss = 1.19928
Iter 35102, loss = 1.25531
Iter 35103, loss = 1.13988
Iter 35104, loss = 0.682343
Iter 35105, loss = 0.942225
Iter 35106, loss = 0.852476
Iter 35107, loss = 0.871301
Iter 35108, loss = 0.861421
Iter 3

Iter 35504, loss = 0.785506
Iter 35505, loss = 1.13603
Iter 35506, loss = 1.28363
Iter 35507, loss = 0.931261
Iter 35508, loss = 0.845667
Iter 35509, loss = 0.897476
Iter 35510, loss = 0.897662
Iter 35511, loss = 0.994283
Iter 35512, loss = 0.903061
Iter 35513, loss = 0.8117
Iter 35514, loss = 0.509192
Iter 35515, loss = 1.263
Iter 35516, loss = 1.12577
Iter 35517, loss = 0.575656
Iter 35518, loss = 1.44751
Iter 35519, loss = 0.846443
Iter 35520, loss = 0.748862
Iter 35521, loss = 0.989167
Iter 35522, loss = 1.0337
Iter 35523, loss = 0.613315
Iter 35524, loss = 1.06152
Iter 35525, loss = 0.987513
Iter 35526, loss = 0.928696
Iter 35527, loss = 0.801678
Iter 35528, loss = 0.685636
Iter 35529, loss = 1.13966
Iter 35530, loss = 0.929556
Iter 35531, loss = 1.35426
Iter 35532, loss = 1.36942
Iter 35533, loss = 1.04881
Iter 35534, loss = 0.993956
Iter 35535, loss = 0.804689
Iter 35536, loss = 0.558736
Iter 35537, loss = 0.875685
Iter 35538, loss = 0.738082
Iter 35539, loss = 0.777406
Iter 355

### Creating Train, Validation, and Test set

Randomly shuffling the complete dataset, and then splitting it into train, validation and test set

In [14]:
shuffled_indices = np.arange(len(eng))
np.random.shuffle(shuffled_indices)

shuffled_vectorized_eng = []
shuffled_vectorized_beng = []

for i in xrange(len(eng)):
    shuffled_vectorized_eng.append(vectorized_eng[shuffled_indices[i]])
    shuffled_vectorized_beng.append(vectorized_beng[shuffled_indices[i]])

train_len = int(.75*len(eng))
val_len = int(.15*len(eng))

train_eng = shuffled_vectorized_eng[0:train_len]
train_beng = shuffled_vectorized_beng[0:train_len]

val_eng = shuffled_vectorized_eng[train_len:val_len]
val_beng = shuffled_vectorized_beng[train_len:val_len]

test_eng = shuffled_vectorized_eng[train_len+val_len:]
test_beng = shuffled_vectorized_beng[train_len+val_len:]

### Function for bucketing and generating batches

Mini-batch training requires all lines in a batch to be of equal length.
We have different lines of different lengths. 

Solution is to fill shorter sentences with PADs so that length of all sentences become equal.
But, if one sentence in a batch has 20 words, and the same batch has another sentence with one word, then the latter sentence will have to be filled in by at least 19 pads. If most of the sentences start to have more PADs than actual content, training will become troublesome.

The solution to that is bucketing. First the sentences in the total list are sorted. After that sentences of similar lengths are closer to each other. Batches are then formed with sentences of similar lengths. Much less padding will be required to turning sentences of similar lengths into senetences of equal lengths. 

In [15]:
def bucket_and_batch(x,y,batch_size):
    
    len_x= np.zeros((len(x)),np.int32)
    
    for i in xrange(len(x)):
        len_x[i] = len(x[i])
        
    sorted_by_len_indices = np.flip(np.argsort(len_x),0)

    sorted_x = []
    sorted_y = []
    
    for i in xrange(len(x)):
        sorted_x.append(x[sorted_by_len_indices[i]])
        sorted_y.append(y[sorted_by_len_indices[i]])
        
    i=0
    batches_x = []
    batches_y = []
    
    while i<len(x):
        
        if i+batch_size>=len(x):
            break
        
        batch_x = []
        batch_y = []
    
        max_len_x = len(sorted_x[i])
    
        len_y= np.zeros((len(y)),np.int32)
    
        for j in xrange(i,i+batch_size):
            len_y[j] = len(sorted_y[j])
            
        max_len_y = np.amax(len_y)
        
        for j in xrange(i,i+batch_size):
            line=[]
            for k1 in xrange(max_len_x+1): #+1 to include <EOS>
                if k1==len(sorted_x[j]):
                    line.append(np_embedding_eng[vocab_eng.index('<EOS>')])
                elif k1>len(sorted_x[j]):
                    line.append(np_embedding_eng[vocab_eng.index('<PAD>')])
                else:
                    line.append(np_embedding_eng[sorted_x[j][k1]])
            batch_x.append(line)
        
            line=[]
            for k2 in xrange(max_len_y+1): #+1 to include <EOS>
                if k2>len(sorted_y[j]):
                    line.append(vocab_beng.index('<PAD>'))
                elif k2==len(sorted_y[j]):
                    line.append(vocab_beng.index('<EOS>'))
                else:
                    line.append(sorted_y[j][k2])
            batch_y.append(line)
    
        batch_x = np.asarray(batch_x,np.float32)
        batch_y = np.asarray(batch_y,np.int32)

        batches_x.append(batch_x)
        batches_y.append(batch_y)
    
        i+=batch_size
        
    return batches_x,batches_y



### Creating train, validation and test batches

In [16]:
batch_size = 64

train_batch_eng,train_batch_beng = bucket_and_batch(train_eng,train_beng,batch_size)

val_batch_eng,val_batch_beng = bucket_and_batch(val_eng,val_beng,batch_size)

test_batch_eng,test_batch_beng = bucket_and_batch(test_eng,test_beng,batch_size)


### Saving processed data in another file.

In [17]:
#Saving processed data in another file.

import pickle

PICK = [vocab_eng,vocab_beng,np_embedding_eng,np_embedding_beng,train_batch_eng,train_batch_beng,val_batch_eng,val_batch_beng,test_batch_eng,test_batch_beng]

with open('translationPICKLE', 'wb') as fp:
    pickle.dump(PICK, fp)